In [10]:
#importing libraries

import pandas as pd
import datetime
from datetime import date, timedelta
import gspread
import pygsheets
from oauth2client.service_account import ServiceAccountCredentials
import warnings
warnings.filterwarnings("ignore")

#creating connections

scope= ['https://spreadsheets.google.com/feeds','https://www.googleapis.com/auth/drive']
credentials= ServiceAccountCredentials.from_json_keyfile_name('client_secret.json', scope) 
client= gspread.authorize(credentials)
clients = pygsheets.authorize(service_file='client_secret.json')

#sheets and code
newleasingmaster='1D0U02U0QN7pXsgM4AdOUiUKB4rB-SoTwSspWkuwl_8E'

sheet= client.open_by_key(newleasingmaster)
ws= sheet.worksheet('Leasing Payment')
data = ws.get_all_values()
headers=data.pop(0)
leasing_payments = pd.DataFrame(data,columns=headers)
leasing_payment=leasing_payments.loc[leasing_payments['Confirmed?'] == 'Yes']
lsp_df=leasing_payment.iloc[:,[2,1,8,8,4,3,5,6,9]]
cols = []
count = 1
for column in lsp_df.columns:
    if column == 'Types of payment':
        cols.append(f'Types of payment{count}')
        count+=1
        continue
    cols.append(column)
lsp_df.columns = cols
lsp_df.rename({'Date':'Date of payment','Types of payment1': 'Types of payment','Types of payment2':'online'}, axis=1, inplace=True)
lsp_df['online'] = lsp_df['online'].str.capitalize()
lsp_df['online'] = lsp_df['online'].apply(lambda x : 'Cash' if x == 'Cash' else '' if x == '' else 'Online')
lsp_df.rename({'Date of payment':'Date  of Payment','Rent or Deposit?':'Collection of Purpose','Types of payment':'Mode Of Payment','online':'Cash/Online','Name':'Name of Employee','ETM ID':'Employee ID','Phone Number':'Mobile','DM name':'DM Name'}, axis=1, inplace=True)

sheet= client.open_by_key(newleasingmaster)
ws= sheet.worksheet('Recovery')
data = ws.get_all_values()
headers=data.pop(0)
recovery = pd.DataFrame(data,columns=headers)
recovery_df=recovery.iloc[:,[0,2,3,4,5,6,7,8,9,10]]
recovery_df['Week Begin date']= recovery_df['Week Begin date'].str.replace('-', '/')
recovery_df['Week Begin date'] = pd.to_datetime(recovery_df['Week Begin date'], errors='coerce',format='%d/%m/%Y')
start_date='2022-06-20'
rec =recovery_df[(recovery_df['Week Begin date'] >= (start_date))]
rec['Week Begin date']=rec['Week Begin date'].astype(str)
recoverys=rec.iloc[:,[1,2,3,4,5,6,7,8,9]]
collection_df = recoverys.append(lsp_df,ignore_index = True)
collection_df.dropna(inplace = True)
sheet= clients.open_by_key(newleasingmaster)
ws= sheet.worksheet_by_title('Testing Abu Salam')
ws.clear(start='A586',end='I100000')
ws.set_dataframe(collection_df,(586,1))
print("New leasing master-collection tab updated successfully")

New leasing master-collection tab updated successfully


Date  of Payment Collection of Purpose Mode Of Payment Cash/Online  \
0          27/12/2021          Leasing Rent           Paytm      Online   
1          27/12/2021       Leasing Deposit           Paytm      Online   
2          27/12/2021       Leasing Deposit           Paytm      Online   
3          27/12/2021       Leasing Deposit            Cash        Cash   
4          27/12/2021          Leasing Rent            Cash        Cash   
...               ...                   ...             ...         ...   
9622       22/06/2022          Leasing Rent           Paytm      Online   
9623       22/06/2022          Leasing Rent           Paytm      Online   
9624       22/06/2022          Leasing Rent           Paytm      Online   
9625       22/06/2022          Leasing Rent           Paytm      Online   
9626       22/06/2022          Leasing Rent           Paytm      Online   

             Name of Employee Employee ID Amount      Mobile       DM Name  
0         Ganesh Dinkar Punde    ETM07270   2000                 Red Eagle  
1               Irshad J Khan    ETM13007  15000              Deadly Shark  
2         Zuber Rehman Shaikh    ETM10432   7000                 Red Eagle  
3         Zuber Rehman Shaikh    ETM10432   6000                 Red Eagle  
4     Shushil Kumar Prajapati    ETM12549  26000                 Red Eagle  
...                       ...         ...    ...         ...           ...  
9622         Pritam R Jaiswal    ETM09717   4200  8828478393     Red Eagle  
9623          Sanket Todankar    ETM20144   2837  8390652527  Deadly Shark  
9624           Sameer Siddqui    ETM15324   4440  9559554433     Red Eagle  
9625         Huzefa Sunelwala    ETM14829   4867  8369183218  Deadly Shark  
9626        Ashutosh Upadhyay    ETM19972   3000  8669006891  Deadly Shark  

[9569 rows x 9 columns]

In [11]:
# pd.set_option("display.max_rows", None)
# collection_df

Date  of Payment   Collection of Purpose  \
0                14/06/2022     Mumbai leasing Rent   
1                14/06/2022     Mumbai leasing Rent   
2                14/06/2022     Mumbai leasing Rent   
3                14/06/2022     Mumbai leasing Rent   
4                14/06/2022  Mumbai Leasing Deposit   
5                14/06/2022     Mumbai leasing Rent   
6                15/06/2022  Mumbai Leasing Deposit   
7                13/06/2022  Mumbai Leasing Deposit   
8                13/06/2022  Mumbai Leasing Deposit   
9                13/06/2022  Mumbai Leasing Deposit   
10               13/06/2022  Mumbai Leasing Deposit   
11               14/06/2022     Mumbai leasing Rent   
12               14/06/2022     Mumbai leasing Rent   
13               14/06/2022     Mumbai leasing Rent   
14               14/06/2022     Mumbai leasing Rent   
15               15/06/2022     Mumbai leasing Rent   
16               15/06/2022     Mumbai leasing Rent   
17               17/06/2022     Mumbai leasing Rent   
18               17/06/2022  Mumbai Leasing Deposit   
19               18/06/2022  Mumbai Leasing Deposit   
20               18/06/2022  Mumbai Leasing Deposit   
21               18/06/2022     Mumbai leasing Rent   
22               18/06/2022  Mumbai Leasing Deposit   
23               18/06/2022  Mumbai Leasing Deposit   
24               18/06/2022     Mumbai leasing Rent   
25               17/06/2022     Mumbai leasing Rent   
26               17/06/2022     Mumbai leasing Rent   
27               17/06/2022     Mumbai leasing Rent   
28               17/06/2022  Mumbai Leasing Deposit   
29               17/06/2022     Mumbai leasing Rent   
30               17/06/2022     Mumbai leasing Rent   
31               13/06/2022  Mumbai Leasing Deposit   
32               15/06/2022     Mumbai leasing Rent   
33               15/06/2022     Mumbai leasing Rent   
34               15/06/2022  Mumbai Leasing Deposit   
35               15/06/2022     Mumbai leasing Rent   
36               15/06/2022     Mumbai leasing Rent   
37               15/06/2022  Mumbai Leasing Deposit   
38               15/06/2022     Mumbai leasing Rent   
39                6/16/2022     Mumbai leasing Rent   
40                6/16/2022     Mumbai leasing Rent   
41                6/16/2022     Mumbai leasing Rent   
42                6/17/2022     Mumbai leasing Rent   
43                6/17/2022     Mumbai leasing Rent   
44               14/06/2022     Mumbai leasing Rent   
45               15/06/2022     Mumbai leasing Rent   
46               16/06/2022     Mumbai leasing Rent   
47               16/06/2022     Mumbai leasing Rent   
48               10/06/2022     Mumbai leasing Rent   
49               15/06/2022     Mumbai leasing Rent   
50     2022-06-04 14:21:33'     Mumbai leasing Rent   
51     2022-06-11 19:20:18'     Mumbai leasing Rent   
52     2022-06-13 04:31:03'     Mumbai leasing Rent   
53     2022-06-13 11:29:09'     Mumbai leasing Rent   
54     2022-06-13 11:06:16'     Mumbai leasing Rent   
55     2022-06-13 11:40:23'     Mumbai leasing Rent   
56     2022-06-13 11:53:47'     Mumbai leasing Rent   
57     2022-06-13 12:36:03'     Mumbai leasing Rent   
58     2022-06-13 12:53:48'  Mumbai Leasing Deposit   
59     2022-06-13 13:11:11'     Mumbai leasing Rent   
60     2022-06-13 13:11:57'     Mumbai leasing Rent   
61     2022-06-13 13:12:59'     Mumbai leasing Rent   
62     2022-06-13 14:08:24'  Mumbai Leasing Deposit   
63     2022-06-13 15:09:25'  Mumbai Leasing Deposit   
64     2022-06-13 15:27:33'  Mumbai Leasing Deposit   
65     2022-06-13 15:28:07'     Mumbai leasing Rent   
66     2022-06-13 15:49:53'     Mumbai leasing Rent   
67     2022-06-13 17:20:12'  Mumbai Leasing Deposit   
68     2022-06-13 17:30:20'     Mumbai leasing Rent   
69     2022-06-13 17:46:11'     Mumbai leasing Rent   
70     2022-06-13 17:47:52'     Mumbai leasing Rent   
71     2022-06-13 17:57:22'     Mumbai leasing Rent

In [84]:
lsp_df

Date of payment Rent or Deposit? Types of payment  online  \
0          27/12/2021     Leasing Rent            Paytm  Online   
1          27/12/2021  Leasing Deposit            Paytm  Online   
2          27/12/2021  Leasing Deposit            Paytm  Online   
3          27/12/2021  Leasing Deposit             Cash    Cash   
4          27/12/2021     Leasing Rent             Cash    Cash   
...               ...              ...              ...     ...   
12302                                                             
12303                                                             
12304                                                             
12305                                                             
12306                                                             

                          Name    ETM ID Amount Phone Number Car Number  \
0          Ganesh Dinkar Punde  ETM07270   2000                           
1                Irshad J Khan  ETM13007  15000                           
2          Zuber Rehman Shaikh  ETM10432   7000                           
3          Zuber Rehman Shaikh  ETM10432   6000                           
4      Shushil Kumar Prajapati  ETM12549  26000                           
...                        ...       ...    ...          ...        ...   
12302                                                                     
12303                                                                     
12304                                                                     
12305                                                                     
12306                                                                     

            DM name  
0         Red Eagle  
1      Deadly Shark  
2         Red Eagle  
3         Red Eagle  
4         Red Eagle  
...             ...  
12302                
12303                
12304                
12305                
12306                

[12307 rows x 10 columns]

In [73]:
lsp_df['online'].unique()

array(['Online', 'Cash', ''], dtype=object)

In [24]:
#importing libraries

import pandas as pd
import datetime
from datetime import date, timedelta
import gspread
import pygsheets
from oauth2client.service_account import ServiceAccountCredentials
import warnings
warnings.filterwarnings("ignore")

#creating connections

scope= ['https://spreadsheets.google.com/feeds','https://www.googleapis.com/auth/drive']
credentials= ServiceAccountCredentials.from_json_keyfile_name('client_secret.json', scope) 
client= gspread.authorize(credentials)
clients = pygsheets.authorize(service_file='client_secret.json')

#sheets and code
newleasingmaster='1D0U02U0QN7pXsgM4AdOUiUKB4rB-SoTwSspWkuwl_8E'

sheet= client.open_by_key(newleasingmaster)
ws= sheet.worksheet('Leasing Payment')
data = ws.get_all_values()
headers=data.pop(0)
leasing_payment = pd.DataFrame(data,columns=headers)
leasing_payment.loc[leasing_payment['Confirmed?'] == 'Yes']
# df.loc[df['points'] == 7]
# lsp_df=leasing_payment.iloc[:,[2,1,8,8,4,3,5,6,7,9]]
# lsp_df

Timestamp Rent or Deposit?        Date    ETM ID  \
0     27/12/2021 11:13:23     Leasing Rent  27/12/2021  ETM07270   
1     27/12/2021 23:27:21  Leasing Deposit  27/12/2021  ETM13007   
2     27/12/2021 23:34:12  Leasing Deposit  27/12/2021  ETM10432   
3     27/12/2021 23:36:07  Leasing Deposit  27/12/2021  ETM10432   
4     27/12/2021 23:37:02     Leasing Rent  27/12/2021  ETM12549   
...                   ...              ...         ...       ...   
9435           18/06/2022  Leasing Deposit  18/06/2022  ETM21965   
9436           18/06/2022     Leasing Rent  18/06/2022  ETM13276   
9437           18/06/2022     Leasing Rent  18/06/2022  ETM15989   
9438           18/06/2022  Leasing Deposit  18/06/2022  ETM01262   
9439           18/06/2022     Leasing Rent  18/06/2022  ETM05302   

                         Name Amount Phone Number Car Number  \
0         Ganesh Dinkar Punde   2000                           
1               Irshad J Khan  15000                           
2         Zuber Rehman Shaikh   7000                           
3         Zuber Rehman Shaikh   6000                           
4     Shushil Kumar Prajapati  26000                           
...                       ...    ...          ...        ...   
9435                     #N/A  15000                           
9436             Anand Tiwari   2900   7046288537              
9437           Prafull Shinde   1720   9324435787              
9438                MD Shamim  15000   9525700782              
9439            Pramod Mohite   2000   7620147908              

      Types of payment       DM name Confirmed?                     
0                Paytm     Red Eagle        Yes  ETM07270           
1                Paytm  Deadly Shark        Yes  ETM13007           
2                Paytm     Red Eagle        Yes  ETM10432           
3                 Cash     Red Eagle        Yes  ETM10432           
4                 Cash     Red Eagle        Yes  ETM12549           
...                ...           ...        ...       ... .. .. ..  
9435             Paytm          #N/A        Yes  ETM21965           
9436             Paytm     Red Eagle        Yes  ETM13276           
9437             Paytm  Deadly Shark        Yes  ETM15989           
9438             Paytm          #N/A        Yes  ETM01262           
9439  Bank Transferred     Red Eagle        Yes  ETM05302           

[9388 rows x 15 columns]

In [44]:
sheet= clients.open_by_key(newleasingmaster)
ws= sheet.worksheet_by_title('Testing Abu Salam')
ws.clear(start='A586',end='I100000')
# ws.set_dataframe(collection_df,(586,1))